# Kaggle survey

Info about the competition: https://www.kaggle.com/competitions/kaggle-survey-2022/overview


In [1]:
# Install ipyvizzu and ipyvizzu-story if you haven't already
#!pip install -U ipyvizzu
#!pip install -U ipyvizzu-story

In [2]:
import pandas as pd
import numpy as np

from ipyvizzu import Chart, Data, Config, Style
from ipyvizzustory import Story, Slide, Step

#Create data object, read csv to data frame and add data frame to data object.
data = Data()

#Only use columns you'll need for your story - should be updated to match the story content
col_list = ['Q2','Q3','Q5','Q23','Q25','Q29','Q44_1']

df = pd.read_csv("../data/Kaggle/kaggle_survey_2022_responses.csv", usecols=col_list)

df.rename(columns={"Q2": "Age", "Q3": "Gender", "Q5": "Student_employee", "Q23": "Title", "Q25": "Company_size", "Q29": "Salary"}, inplace = True)
#Add count column
df['Count'] = 1
df['Company_size'] = df['Company_size'].str.replace('employees','')
df.head()

Age                                  Gender  \
0  What is your age (# years)?  What is your gender? - Selected Choice   
1                        30-34                                     Man   
2                        30-34                                     Man   
3                        18-21                                     Man   
4                        55-59                                     Man   

                                    Student_employee  \
0  Are you currently a student? (high school, uni...   
1                                                 No   
2                                                 No   
3                                                Yes   
4                                                 No   

                                               Title  \
0  Select the title most similar to your current ...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                     Data Scientist   

                                        Company_size  \
0  What is the size of the company where you are ...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                              0-49    

                                              Salary  \
0  What is your current yearly compensation (appr...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                      25,000-29,999   

                                               Q44_1  Count  
0  Who/what are your favorite media sources that ...      1  
1                                                NaN      1  
2                                                NaN      1  
3                 Twitter (data science influencers)      1  
4                 Twitter (data science influencers)      1

In [3]:
#Remove row with question texts
df = df.drop(0)

In [4]:
#Add new column categorizing respondents with ages above and below 30
df.insert(1,'age_30',np.where((df.Age == '18-21') | (df.Age == '22-24') | (df.Age == '25-29'), "below 30", "above 30"))
df['age_30'] = df['age_30'].astype(str)

In [5]:
#Add percentage value for gender categories for each age group
df['Gender_added'] = df['Gender'].notna()
df['Gender_added'] = df['Gender_added'].astype(str)
df['Gender_Pct[%]'] = 100 / df.groupby(['age_30','Gender_added'])['Count'].transform('sum') 

In [6]:
#Replace values in Student_employee column for easier understanding when values shown on the legend
df.Student_employee.replace({'Yes': 'Student', 'No': 'Employee'}, inplace = True)
df.head()

Age    age_30 Gender Student_employee           Title Company_size  \
1  30-34  above 30    Man         Employee             NaN          NaN   
2  30-34  above 30    Man         Employee             NaN          NaN   
3  18-21  below 30    Man          Student             NaN          NaN   
4  55-59  above 30    Man         Employee  Data Scientist        0-49    
5  45-49  above 30    Man          Student             NaN          NaN   

          Salary                               Q44_1  Count Gender_added  \
1            NaN                                 NaN      1         True   
2            NaN                                 NaN      1         True   
3            NaN  Twitter (data science influencers)      1         True   
4  25,000-29,999  Twitter (data science influencers)      1         True   
5            NaN                                 NaN      1         True   

   Gender_Pct[%]  
1       0.009361  
2       0.009361  
3       0.007511  
4       0.009361  
5       0.009361

In [7]:
df.Company_size.unique()

array([nan, '0-49 ', '250-999 ', '1000-9,999 ', '10,000 or more ',
       '50-249 '], dtype=object)

In [8]:
#sort the dataframe by title
titlesorter = ['Data Scientist', 'Data Analyst', 'Software Engineer', 'Teacher / professor', 'Manager', 'Other', 'Research Scientist', 'ML / MLops Engineer', 'Engineer (non-software)', 'Data Engineer', 'Statistician', 'Data Architect', 'Data Administrator', 'Developer Advocate', 'Currently not employed',]

#replace long titles with shorter versions
df = df.replace("Data Analyst (Business, Marketing, Financial, Quantitative, etc)", "Data Analyst")
df = df.replace("Manager (Program, Project, Operations, Executive-level, etc)", "Manager")
df = df.replace("Machine Learning/ MLops Engineer", "ML / MLops Engineer")
df = df.replace("Currently not employed", "Unemployed")
df = df.replace("Engineer (non-software)", "Other Engineer")

# Create the dictionary that defines the order for sorting
sorterIndex = dict(zip(titlesorter, range(len(titlesorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Title_Rank'] = df['Title'].map(sorterIndex)
# the actual sorting is done together with salary, title below

In [9]:
#Add percentage share value between age groups for each title
df['Employee_w_title'] = df['Title'].notna()
df['Employee_w_title'] = df['Employee_w_title'].astype(str)
df.Employee_w_title.replace({'True': 'Added title', 'False': 'No info'}, inplace = True)
df['Title_Pct[%]'] = 100 / df.groupby(['Title','Employee_w_title'])['Count'].transform('sum')


In [10]:
df['Employee_w_title'].value_counts()

No info        13367
Added title    10630
Name: Employee_w_title, dtype: int64

In [11]:
df['Title'].value_counts()

Data Scientist         1929
Data Analyst           1538
Unemployed             1432
Software Engineer       980
Teacher / professor     833
Manager                 832
Other                   754
Research Scientist      593
ML / MLops Engineer     571
Other Engineer          465
Data Engineer           352
Statistician            125
Data Architect           95
Data Administrator       70
Developer Advocate       61
Name: Title, dtype: int64

In [12]:
df.groupby(['age_30','Employee_w_title']).size()

age_30    Employee_w_title
above 30  Added title         7198
          No info             3485
below 30  Added title         3432
          No info             9882
dtype: int64

In [13]:
#sort the dataframe by company size
sizesorter = ['0-49', '50-249', '250-999', '1000-9,999', '10,000 or more', 'NaN']

# Create the dictionary that defines the order for sorting
sorterIndex2 = dict(zip(sizesorter, range(len(sizesorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Size_Rank'] = df['Company_size'].map(sorterIndex2)

# the actual sorting is done together with salary, title below

In [14]:
#Add column to seperate those that did not add company size
df['Employee_w_size'] = df['Company_size'].notna()
df['Employee_w_size'] = df['Employee_w_size'].astype(str)
df.Employee_w_size.replace({'True': 'Added company size', 'False': 'No info'}, inplace = True)
df['Size_Pct[%]'] = 100 / df.groupby(['age_30','Employee_w_size'])['Count'].transform('sum')

In [15]:
#Add new column to have fewer salary categories
salary_map = {'$0-999': '$0-1k',
                '1,000-1,999': '$1-10k',
                '2,000-2,999': '$1-10k',
                '3,000-3,999': '$1-10k',
                '4,000-4,999': '$1-10k',
                '5,000-7,499': '$1-10k',
                '7,500-9,999': '$1-10k',
                '10,000-14,999': '$10-20k',
                '15,000-19,999': '$10-20k',
                '20,000-24,999': '$20-50k',
                '25,000-29,999': '$20-50k',
                '30,000-39,999': '$20-50k',
                '40,000-49,999': '$20-50k',
                '50,000-59,999': '$50-100k',
                '60,000-69,999': '$50-100k',
                '70,000-79,999': '$50-100k',
                '80,000-89,999': '$50-100k',
                '90,000-99,999': '$50-100k',
                '100,000-124,999': '$100-200k',
                '125,000-149,999': '$100-200k',
                '150,000-199,999': '$100-200k',
                '200,000-249,999': '$200-500k',
                '250,000-299,999': '$200-500k',
                '300,000-499,999': '$200-500k',
                '$500,000-999,999': '$500k-1M',
                '>$1,000,000': '$1M+'}

df['salary_cat'] = df['Salary'].map(salary_map)

In [16]:
#prepare to sort the dataframe by salary list
salarysorter = ['$0-1k', '$1-10k', '$10-20k', '$20-50k', '$50-100k', '$100-200k', '$200-500k', '$500k-1M', '$1M+', 'NaN']

# Create the dictionary that defines the order for sorting
sorterIndex3 = dict(zip(salarysorter, range(len(salarysorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Salary_Rank'] = df['salary_cat'].map(sorterIndex3)

#sorting based on all of the rankings
df.sort_values(['Salary_Rank','Title_Rank','Size_Rank'], inplace = True)

In [17]:
#Add percentage value for salary categories for each age group
df['Employee_w_salary'] = df['salary_cat'].notna()
df['Employee_w_salary'] = df['Employee_w_salary'].astype(str)
df.Employee_w_salary.replace({'True': 'Added salary', 'False': 'No info'}, inplace = True)
df['Salary_Pct[%]'] = 100 / df.groupby(['age_30','Employee_w_salary'])['Count'].transform('sum')

display(df)

Age    age_30 Gender Student_employee           Title Company_size  \
115    30-34  above 30    Man         Employee  Data Scientist        0-49    
255    30-34  above 30  Woman         Employee  Data Scientist      50-249    
329    22-24  below 30  Woman         Employee  Data Scientist     250-999    
839    30-34  above 30    Man         Employee  Data Scientist        0-49    
1168   25-29  below 30    Man         Employee  Data Scientist        0-49    
...      ...       ...    ...              ...             ...          ...   
23989  55-59  above 30    Man          Student             NaN          NaN   
23992  22-24  below 30    Man          Student             NaN          NaN   
23993  22-24  below 30    Man          Student             NaN          NaN   
23994  60-69  above 30    Man          Student             NaN          NaN   
23997  18-21  below 30    Man          Student             NaN          NaN   

       Salary Q44_1  Count Gender_added  ...  Title_Rank  Employee_w_title  \
115    $0-999   NaN      1         True  ...         0.0       Added title   
255    $0-999   NaN      1         True  ...         0.0       Added title   
329    $0-999   NaN      1         True  ...         0.0       Added title   
839    $0-999   NaN      1         True  ...         0.0       Added title   
1168   $0-999   NaN      1         True  ...         0.0       Added title   
...       ...   ...    ...          ...  ...         ...               ...   
23989     NaN   NaN      1         True  ...         NaN           No info   
23992     NaN   NaN      1         True  ...         NaN           No info   
23993     NaN   NaN      1         True  ...         NaN           No info   
23994     NaN   NaN      1         True  ...         NaN           No info   
23997     NaN   NaN      1         True  ...         NaN           No info   

      Title_Pct[%]  Size_Rank     Employee_w_size Size_Pct[%]  salary_cat  \
115        0.05184        NaN  Added company size    0.015793       $0-1k   
255        0.05184        NaN  Added company size    0.015793       $0-1k   
329        0.05184        NaN  Added company size    0.036576       $0-1k   
839        0.05184        NaN  Added company size    0.015793       $0-1k   
1168       0.05184        NaN  Added company size    0.036576       $0-1k   
...            ...        ...                 ...         ...         ...   
23989          NaN        NaN             No info    0.022983         NaN   
23992          NaN        NaN             No info    0.009452         NaN   
23993          NaN        NaN             No info    0.009452         NaN   
23994          NaN        NaN             No info    0.022983         NaN   
23997          NaN        NaN             No info    0.009452         NaN   

      Salary_Rank  Employee_w_salary Salary_Pct[%]  
115           0.0       Added salary      0.017525  
255           0.0       Added salary      0.017525  
329           0.0       Added salary      0.041152  
839           0.0       Added salary      0.017525  
1168          0.0       Added salary      0.041152  
...           ...                ...           ...  
23989         NaN            No info      0.020092  
23992         NaN            No info      0.009188  
23993         NaN            No info      0.009188  
23994         NaN            No info      0.020092  
23997         NaN            No info      0.009188  

[23997 rows x 21 columns]

In [18]:
style = Style({
    'fontSize':'120%',
    'logo':{'width':'5em'},
        'legend':{'width': '14em'},
        'title' : {'fontSize' : '2em'},
        'plot' : {
            'marker' :{ 'label' :{ 'maxFractionDigits' : 1},'maxLightness' : 0,},
            'xAxis' :{ 'title' :{ 'color' : '#00000000'}},
            'yAxis' :{ 'title' :{ 'color' : '#00000000'}}
        }
})

In [19]:
data.add_data_frame(df)
story = Story(data=data, style=style)
story.set_size("100%", "400px")
story.set_feature("tooltip", True)

slide1 = Slide(
#Show number of respondents
    Step(
        Config({
            "x": "Count",
            "label":"Count",
         #   "reverse": True,
            "title": "Almost 24 thousand people filled the survey",

        })
    )
)
story.add_slide(slide1)

slide2 = Slide()
#Show number of respondents below and above 30
slide2.add_step(
    Step(
        Config({
            "x": ["age_30","Count"],
            "label":"age_30"
        })
))

slide2.add_step(
    Step(
        Config({
            "x": "Count",
            "y": "age_30",
            "label":"Count",
            "title": "55% of respondents are younger than 30"
        })
    )
)
story.add_slide(slide2)

#Add gender
slide3 = Slide()

slide3.add_step(
    Step(
        Config({
            "x": ["Count","Gender"],
            "y": "age_30",
        })
    )
)

slide3.add_step(
    Step(
        Config({
            "color":"Gender",
        }),
        Style({'plot' : {'marker' : { 'colorPalette' : '#03AE71FF #F4941BFF #F4C204FF #D49664FF #F25456FF'}}})
    )
)
    

#Show ratio of genders
slide3.add_step(
    Step(
        Config({
            'align':'stretch',
            'label':'Gender_Pct[%]',
            "title": "There are a bit more women in the younger generations"
        })
    )
)
story.add_slide(slide3)

In [20]:
#Add event to avoid small values written on the label scale as they overlap
label_handler_method = """let parts = event.data.text.split(' ');
if (parts[1] == '%') {
	if (parts[0] < 2) event.preventDefault();
} else if (parts[1] == undefined) {
	if (parts[0] < 200) event.preventDefault();
}"""
story.add_event("plot-marker-label-draw", label_handler_method)

In [21]:
#Remove gender
slide4 = Slide()

slide4.add_step(
    Step(
        Config({
            "align": "none",
            "label": "Count",
            "title": "Let's see what they do for a living"
        })
    )
)

slide4.add_step(
    Step(
        Config({
            "x":"Count",
            "color":None,
            "legend":"lightness"
        }),
        Style({'plot' : {'marker' : { 'colorPalette' : None}}})
    )
)

#Add student/employee status

slide4.add_step(
    Step(
        Config({
            "x": ["Count","Student_employee"],
            "y": "age_30",
            "color":"Student_employee",
            "title": "70% below 30 vs. 25% above 30 are students",
            "legend":"color"
        }),
        Style({'legend':{'width': '12.5em'}, "plot": {"marker": {"colorPalette": "#00819CFF #C08030FF" }}})
    )
)

story.add_slide(slide4)

#Zoom to those who are not students anymore
slide5 = Slide()
slide5.add_step(
    Step(
        Config({
            "title": "Let's focus on the employees"
        })
    )
)
slide5.add_step(
    Step(
        Data.filter("record.Student_employee == 'Employee'"),
    )
)

slide5.add_step(
    Step(
        Config({
            "color": "age_30",
            "legend":"color",
            "title": "All employees"
        }),
        Style({"plot": {
            "marker": {"colorPalette": "#26B6C3FF #453A90FF" },
            'yAxis' : { 'label' :{ 'color' : '#00000000'}}
        }})
))
            

story.add_slide(slide5)

In [22]:
slide6 = Slide()

slide6.add_step(
    Step(
        Config({
            "title": "Let's see the size of the companies they work for"
        })
    )
)

slide6.add_step(
    Step(
        Config({
            "x": ["Count","Employee_w_size"],
            "label":"Employee_w_size",
            "color":["age_30","Employee_w_size"]
        }),
        Style({"plot": {"marker": {"colorPalette": "#26B6C3FF #DCD9EAFF #453A90FF #C8C4DFFF"}}})
    )
)

slide6.add_step(
    Step(
        Data.filter("record.Student_employee === 'Employee' && record.Employee_w_size === 'Added company size'" ),
    )
)

slide6.add_step(
    Step(
        Config({
            "x": ["Count","Company_size"],
            "label":"Size_Pct[%]",
        })
    )
)

slide6.add_step(
    Step(
        Config({
            "geometry":"circle",
            "x": {"set":"Company_size","range": {"max": "6"}},
            "label":"Size_Pct[%]",
            "size":"Size_Pct[%]",
            "title": "Most youngsters work at very big or very small companies"
        }),Style({ 'paddingBottom' : '2em',
        'plot' : {'xAxis' :{ 'label' :{ 'angle' : '-0.785','paddingTop' : '0'}}, 
                 'marker' : { 'label' :{ 'position' : 'center'},'circleMaxRadius' : '0.14', 'circleMinRadius' : '0.07'}, 
                 }})
    )
) 

story.add_slide(slide6)

slide7 = Slide()
slide7.add_step(
    Step(
        Config(({
            "size":None,
            "x": {"set":["Count","Company_size"],"range": {"max": "auto"}},
            "title": "",
            "geometry":"rectangle"
        })
    )
))

slide7.add_step(
    Step(
        Config(({
            "x": ["Count","Employee_w_size"],
            "label":"Employee_w_size",
            "color":["age_30","Employee_w_size"]
        })
    )
))

slide7.add_step(
    Step(
        Data.filter("record.Student_employee === 'Employee'" ),
    )
)

slide7.add_step(
    Step(
        Config({
            "x":"Count",
            "label":"Count",
            "color": "age_30",
            "legend":"color",
            "title": "All employees"
        }),
        Style({"plot": {"marker": {"colorPalette": "#26B6C3FF #453A90FF" }}})
    )
)

story.add_slide(slide7)

In [23]:
slide8 = Slide()

slide8.add_step(
    Step(
        Config({
            "title": "Let's check out the salaries"
        })
    )
)


slide8.add_step(
    Step(
        Config({
            "x": ["Count","Employee_w_salary"],
            "label":"Employee_w_salary",
            "color":["age_30","Employee_w_salary"]
        }),
        Style({"plot": {"marker": {"colorPalette": "#26B6C3FF #DCD9EAFF #453A90FF #C8C4DFFF"}}})
    )
)

slide8.add_step(
    Step(
        Data.filter("record.Student_employee === 'Employee' && record.Employee_w_salary === 'Added salary'" ),
    )
)

slide8.add_step(
    Step(
        Config({
            "x": ["Count","salary_cat"],
            "label":None,
        }),
    )
)

slide8.add_step(
    Step(
        Config({
            "y":["Salary_Pct[%]","age_30"],
            "x":"salary_cat",
            "split": True,
            "title":"Over 50% below 30 earns less than $10k per year",
        })
    )
)
slide8.add_step(
    Step(
        Config({
            "label":"Salary_Pct[%]"
        })
    )
)

story.add_slide(slide8)

In [24]:
slide9 = Slide()

slide9.add_step(
    Step(
        Config({
            "x": ["Count","salary_cat"],
            "y": "age_30",
            "split": False
        }),
))

slide9.add_step(
    Step(
        Config({
            "label": "Employee_w_salary",
            "x": ["Count","Employee_w_salary"]
        })
    )
)

slide9.add_step(
    Step(
        Data.filter("record.Student_employee === 'Employee'"),
    )
)

slide9.add_step(
    Step(
        Config({
            "x":"Count",
            "label":"Count",
            "color": "age_30",
            "legend":"color",
            "title": "All employees"
        }),
        Style({"plot": {"marker": {"colorPalette": "#26B6C3FF #453A90FF" }}})
    )
)

story.add_slide(slide9)

slide10 = Slide()

slide10.add_step(
    Step(
        Config({
            "title": "Finally, let's see the titles!"
        })
    )
)


slide10.add_step(
    Step(
        Config({
            "x": ["Count","Employee_w_title"],
            "label":"Employee_w_title",
            "color":["age_30","Employee_w_title"]
        }),
        Style({"plot": {"marker": {"colorPalette": "#26B6C3FF #DCD9EAFF #453A90FF #C8C4DFFF"}}})
    )
)

slide10.add_step(
    Step(
        Data.filter("record.Student_employee === 'Employee' && record.Employee_w_title === 'Added title'" ),
    )
)

slide10.add_step(
    Step(
        Config({
            "x": ["Count","Title"],
            "label":None,
        }),
    )
)

slide10.add_step(
    Step(
        Config({
            "x": "Title",
            "y": ["age_30","Count"],
            "label":"Count",
            "title":"39% below 30 vs. 30% above 30 works as Data Scientist or Data Analyst"
        }),
        Style({'plot' : {'paddingBottom' : '10em'}})
    )
)

story.add_slide(slide10)

In [25]:
slide11 = Slide()
slide11.add_step(
    Step(
        Config({
 #           "y": ["age_30","Count"],
            "align":"stretch",
            "label":"Title_Pct[%]",
            "title":"Many ML/MLOps engineers and very few Data Architects are below 30",
            "sort":"byValue",
        }),
        Style({'plot' : {'marker' :{ 'label' :{ 'maxFractionDigits' : 0, 'fontSize': '90%'}}}}
        )
    )
)
story.add_slide(slide11)

# Play the created story - should be at the end of the cell
story.play()

In [26]:
# If you want to save the story as an interactive HTML
# (containing only the output of the previous cell),
# use the following command:
#story.export_to_html(filename="../html/kaggle.html")

### Learn more about [ipyvizzu-story](https://github.com/vizzuhq/ipyvizzu-story/)